In [ ]:
from classes.exchange import ForexDataHandler

forex_handler = ForexDataHandler()
currency_pairs = [
    ('CNY', 'RUB'),  # Китайский юань
    ('USD', 'RUB'),  # Доллар США
    ('EUR', 'RUB'),  # Евро
    ('GBP', 'RUB'),  # Фунт стерлингов
    ('JPY', 'RUB'),  # Японская йена
    ('KZT', 'RUB'),  # Казахстанский тенге
    ('UAH', 'RUB'),  # Украинская гривна
    ('BYN', 'RUB'),  # Белорусский рубль
]

try:
    print("\nТекущие курсы валют:")
    for base_currency, quote_currency in currency_pairs:
        try:
            rate = forex_handler.get_forex_rate(base_currency, quote_currency)
            print(f"\nКурс {base_currency}/{quote_currency}:")
            print(f"Текущий: {rate['close']:.4f}")      
            print(f"Дата: {rate['timestamp']}")
        except Exception as pair_error:
            print(f"Ошибка при получении курса {base_currency}/{quote_currency}: {pair_error}")
            
except Exception as e:
    print(f"Произошла ошибка: {e}")

In [ ]:
from classes.moex_class import RussianMarketData

market_data = RussianMarketData()

# Получение исторических данных для сектора нефти и газа
oil_gas_index = market_data.get_historical_data('oil_gas')
print("\nИндекс нефти и газа Мосбиржи:")
print(oil_gas_index.head())
print(f"\nВсего записей: {len(oil_gas_index)}")

In [4]:
import requests

# Базовый URL для API Мосбиржи
base_url = "https://iss.moex.com/iss"

def get_moex_indices():
    """
    Получение списка индексов Мосбиржи
    """
    # Формируем URL для запроса индексов
    url = f"{base_url}/engines/stock/markets/index/securities.json"
    
    try:
        # Выполняем запрос
        response = requests.get(url)
        response.raise_for_status()  # Проверяем на ошибки
        data = response.json()
        
        # Извлекаем информацию об индексах
        securities = data['securities']
        columns = securities['columns']
        data = securities['data']
        
        # Создаем словарь с информацией об индексах
        indices = {}
        secid_index = columns.index('SECID')
        shortname_index = columns.index('SHORTNAME')
        
        for row in data:
            indices[row[secid_index]] = row[shortname_index]
            
        return indices
        
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении данных: {e}")
        return None

# Получаем и выводим список индексов
indices = get_moex_indices()
if indices:
    print("Список индексов Мосбиржи:")
    for secid, shortname in indices.items():
        print(f"{secid}: {shortname}")

Список индексов Мосбиржи:
2xEQT: iNAV 2xEQT
2xOFZ: iNAV 2xOFZ
AKAIA: iNAV Альфа Антиинфляционный
AKCBI: iАльфа-Капитал Облигации
AKCHA: iNAV Альфа Китайские акции
AKEBA: iNAV Альфа Управляемые евробонды
AKEUA: iNAV Альфа-Капитал ЕВРОПА 600
AKEUBI: AKEUBI
AKFBA: iNAV Альфа Облигации ПК
AKGDA: iNAV Альфа Золото
AKHTA: iNAV Альфа ИТ Лидеры
AKIEA: iNAV Альфа Акции с выпл. дохода
AKMBA: iNAV Альфа Управляемые облигации
AKMDA: iNAV Альфа Медицина
AKMEI: iNAV Альфа Управляемые акции
AKMMA: iNAV Альфа Денежный рынок
AKNXA: iNAV Технологии 100
AKQUA: iNAV Альфа Квант
AKQUB: iNAV Альфа Квант
AKREI: Альфа Капитал Российские Акции
AKREPI: Альфа Капитал РосАкции Ценовой
AKSCA: iNAV Альфа Космос
AKSCB: iNAV Альфа Космос
AKSFA: iNAV Альфа Стратегия Будущего
AKSFPI: AKSFPI
AKSPA: iNAV Альфа - Капитал Эс энд Пи 500
AKSPRU: Индекс Альфа Капитал Космос
AKSPSP: Индекс Альфа Капитал Космос
AKUPA: iNAV Альфа Умный портфель
AKVGA: iNAV Альфа Видеоигры
AKVGB: iNAV Альфа Видеоигры
AKVGRU: Альфа-Капитал Видеоиг

In [7]:
import requests
import pandas as pd

def get_index_constituents(index_id):
    """
    Получение списка компаний, входящих в индекс
    """
    # Используем другой эндпоинт для получения состава индекса
    url = f"https://iss.moex.com/iss/statistics/engines/stock/markets/index/analytics/{index_id}/tickers.json"
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        data = response.json()
        
        # Получаем данные из секции tickers
        if 'tickers' in data:
            tickers = data['tickers']
            df = pd.DataFrame(tickers['data'], columns=tickers['columns'])
            
            # Выводим нужные колонки, если они есть
            needed_columns = []
            if 'ticker' in df.columns:
                needed_columns.append('ticker')
            if 'shortnames' in df.columns:
                needed_columns.append('shortnames')
            if 'weight' in df.columns:
                needed_columns.append('weight')
                
            return df[needed_columns]
        else:
            print(f"Нет данных о составе индекса {index_id}")
            return None
            
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении данных: {e}")
        return None

def get_index_history(index_id):
    """
    Получение исторических значений индекса
    """
    url = f"https://iss.moex.com/iss/history/engines/stock/markets/index/securities/{index_id}.json"
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        data = response.json()
        
        if 'history' in data:
            history = data['history']
            df = pd.DataFrame(history['data'], columns=history['columns'])
            return df
        else:
            print(f"Нет исторических данных для индекса {index_id}")
            return None
            
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении исторических данных: {e}")
        return None

def get_moex_sector_indices():
    """
    Получение отраслевых индексов Мосбиржи
    """
    url = "https://iss.moex.com/iss/engines/stock/markets/index/securities.json"
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        data = response.json()
        
        securities = data['securities']
        df = pd.DataFrame(securities['data'], columns=securities['columns'])
        
        # Фильтруем отраслевые индексы
        sector_indices = df[
            (df['SECID'].str.contains('MOEX', na=False) & 
             ~df['SECID'].str.contains('REPO|EUROBOND', na=False)) |
            (df['SECID'].str.contains('RTS', na=False) & 
             ~df['SECID'].str.contains('REPO|EUROBOND', na=False))
        ]
        
        result = sector_indices[['SECID', 'SHORTNAME', 'NAME']].drop_duplicates()
        
        # Группируем по секторам
        sectors = {
            'Металлы и добыча': result[result['SECID'].str.contains('MM|METL|GOLD|SILV', case=False, na=False)],
            'Нефть и газ': result[result['SECID'].str.contains('OG|OIL|GAS', case=False, na=False)],
            'Химия': result[result['SECID'].str.contains('CH|CHEM', case=False, na=False)],
            'Электроэнергетика': result[result['SECID'].str.contains('EU', case=False, na=False)],
            'Телекоммуникации': result[result['SECID'].str.contains('TL', case=False, na=False)],
            'Финансы': result[result['SECID'].str.contains('FN', case=False, na=False)],
            'Потребительский сектор': result[result['SECID'].str.contains('CN|CR', case=False, na=False)],
            'Транспорт': result[result['SECID'].str.contains('TN', case=False, na=False)]
        }
        
        return sectors
    
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении данных: {e}")
        return None

# Пример использования
sectors = get_moex_sector_indices()
if sectors:
    for sector_name, sector_data in sectors.items():
        print(f"\n{sector_name}:")
        print(sector_data)
        
        if not sector_data.empty:
            first_index = sector_data.iloc[0]['SECID']
            print(f"\nСостав индекса {first_index}:")
            constituents = get_index_constituents(first_index)
            if constituents is not None:
                print(constituents.head())
                
            print(f"\nПоследние значения индекса {first_index}:")
            history = get_index_history(first_index)
            if history is not None:
                print(history[['TRADEDATE', 'CLOSE']].tail())


Металлы и добыча:
      SECID                     SHORTNAME                               NAME
253  MOEXMM      Индекс металлов и добычи  Индекс МосБиржи металлов и добычи
341   RTSMM  Индекс РТС металлов и добычи       Индекс РТС металлов и добычи

Состав индекса MOEXMM:
  ticker
0   ALRS
1   AMEZ
2   BELO
3   BLNG
4   CHEP

Последние значения индекса MOEXMM:
     TRADEDATE    CLOSE
95  2005-05-27  1152.02
96  2005-05-30  1141.46
97  2005-05-31  1160.66
98  2005-06-01  1148.49
99  2005-06-02  1175.16

Нефть и газ:
      SECID                SHORTNAME                          NAME
254  MOEXOG      Индекс нефти и газа  Индекс МосБиржи нефти и газа
342   RTSOG  Индекс РТС нефти и газа       Индекс РТС нефти и газа

Состав индекса MOEXOG:
  ticker
0   BANE
1  BANEP
2   GAZP
3  JNOSP
4  KRKNP

Последние значения индекса MOEXOG:
     TRADEDATE    CLOSE
95  2005-05-27  1123.93
96  2005-05-30  1122.11
97  2005-05-31  1134.91
98  2005-06-01  1136.09
99  2005-06-02  1149.11

Химия:
      SECID

In [8]:
import requests
import pandas as pd

def get_index_constituents(index_id):
    """
    Получение списка компаний, входящих в индекс
    """
    url = f"https://iss.moex.com/iss/statistics/engines/stock/markets/index/analytics/{index_id}/tickers.json"
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        data = response.json()
        
        if 'tickers' in data:
            tickers = data['tickers']
            df = pd.DataFrame(tickers['data'], columns=tickers['columns'])
            
            # Возвращаем только список тикеров
            if 'ticker' in df.columns:
                return df['ticker'].tolist()
            return []
            
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении данных: {e}")
        return []

def get_sector_tickers():
    """
    Формирование словаря секторов и входящих в них тикеров
    """
    url = "https://iss.moex.com/iss/engines/stock/markets/index/securities.json"
    
    try:
        response = requests.get(url)
        response.raise_for_status()
        data = response.json()
        
        securities = data['securities']
        df = pd.DataFrame(securities['data'], columns=securities['columns'])
        
        # Определяем основные секторальные индексы MOEX
        sector_indices = {
            'metals_mining': 'MOEXMM',    # Металлы и добыча
            'oil_gas': 'MOEXOG',          # Нефть и газ
            'chemicals': 'MOEXCH',         # Химия и нефтехимия
            'electric_utilities': 'MOEXEU', # Электроэнергетика
            'telecom': 'MOEXTL',          # Телекоммуникации
            'finance': 'MOEXFN',          # Финансы
            'consumer': 'MOEXCN',         # Потребительский сектор
            'transport': 'MOEXTN'         # Транспорт
        }
        
        # Создаем словарь для хранения тикеров по секторам
        sector_tickers = {}
        
        # Получаем тикеры для каждого сектора
        for sector, index_id in sector_indices.items():
            tickers = get_index_constituents(index_id)
            if tickers:
                sector_tickers[sector] = tickers
            else:
                sector_tickers[sector] = []
                
        return sector_tickers
        
    except requests.exceptions.RequestException as e:
        print(f"Ошибка при получении данных: {e}")
        return None

# Получаем словарь секторов и тикеров
sector_tickers = get_sector_tickers()

if sector_tickers:
    print("Тикеры по секторам:")
    for sector, tickers in sector_tickers.items():
        print(f"\n{sector}:")
        print(tickers)
        print(f"Количество компаний в секторе: {len(tickers)}")

# Пример использования словаря для дальнейшей работы
def get_sector_by_ticker(ticker, sector_dict):
    """
    Поиск сектора по тикеру
    """
    for sector, tickers in sector_dict.items():
        if ticker in tickers:
            return sector
    return None

# Сохранение словаря в файл для дальнейшего использования
import json

def save_sectors_to_file(sector_dict, filename='sector_tickers.json'):
    """
    Сохранение словаря секторов в JSON файл
    """
    with open(filename, 'w', encoding='utf-8') as f:
        json.dump(sector_dict, f, ensure_ascii=False, indent=4)

def load_sectors_from_file(filename='sector_tickers.json'):
    """
    Загрузка словаря секторов из JSON файла
    """
    try:
        with open(filename, 'r', encoding='utf-8') as f:
            return json.load(f)
    except FileNotFoundError:
        print(f"Файл {filename} не найден")
        return None

# Сохраняем данные
if sector_tickers:
    save_sectors_to_file(sector_tickers)

# Пример использования
test_ticker = 'GAZP'  # например
sector = get_sector_by_ticker(test_ticker, sector_tickers)
if sector:
    print(f"\nТикер {test_ticker} относится к сектору: {sector}")
else:
    print(f"\nТикер {test_ticker} не найден в секторальных индексах")

# Статистика по секторам
if sector_tickers:
    print("\nСтатистика по секторам:")
    for sector, tickers in sector_tickers.items():
        print(f"{sector}: {len(tickers)} компаний")

Тикеры по секторам:

metals_mining:
['ALRS', 'AMEZ', 'BELO', 'BLNG', 'CHEP', 'CHMF', 'CHMK', 'CHZN', 'ENPG', 'GMKN', 'KBTK', 'KOGK', 'LNZL', 'LNZLP', 'MAGN', 'MGOK', 'MTLR', 'MTLRP', 'NLMK', 'PGIL', 'PLZL', 'PMTL', 'POGR', 'POLY', 'RASP', 'RUAL', 'RUALR', 'SELG', 'SELGP', 'TRMK', 'UGLD', 'UNKL', 'VSMO', 'VSMZ']
Количество компаний в секторе: 34

oil_gas:
['BANE', 'BANEP', 'GAZP', 'JNOSP', 'KRKNP', 'LKOH', 'MFGS', 'MFGSP', 'NOTK', 'NVTK', 'RITK', 'RNFT', 'RNHSP', 'ROSN', 'SIBN', 'SNGS', 'SNGSP', 'TATN', 'TATNP', 'TNBP', 'TNBPP', 'TRMK', 'TRNFP']
Количество компаний в секторе: 23

chemicals:
['AKRN', 'AZKM', 'DGBZ', 'DGBZP', 'KAZT', 'KZOS', 'KZOSP', 'MGNZ', 'NKNC', 'NKNCP', 'OMSH', 'PHOR', 'SILV', 'URKA', 'YASH']
Количество компаний в секторе: 15

electric_utilities:
['ARSB', 'BEGY', 'DVEC', 'EESR', 'EESRP', 'ELFV', 'ENRU', 'EONR', 'FEES', 'HYDR', 'IRAO', 'IRGZ', 'KISB', 'KRNG', 'KRSG', 'LSNG', 'LSNGP', 'MGSV', 'MRKC', 'MRKH', 'MRKK', 'MRKP', 'MRKS', 'MRKU', 'MRKV', 'MRKY', 'MRKZ', 'MSNG

----
----
----

In [10]:
import pandas as pd
import requests
from datetime import datetime, timedelta
from typing import List, Dict, Optional
import asyncio
import aiohttp
import numpy as np

class MOEXHistoricalData:
    def __init__(self):
        self.base_url = "https://iss.moex.com/iss"
        
    async def get_security_history(
        self,
        ticker: str,
        start_date: str,
        end_date: str,
        engine: str = "stock",
        market: str = "shares",
        board: str = "TQBR"
    ) -> pd.DataFrame:
        """
        Получение исторических данных по отдельному тикеру
        
        Args:
            ticker: Тикер акции
            start_date: Начальная дата в формате YYYY-MM-DD
            end_date: Конечная дата в формате YYYY-MM-DD
            engine: Торговый движок (по умолчанию stock)
            market: Рынок (по умолчанию shares)
            board: Режим торгов (по умолчанию TQBR)
            
        Returns:
            DataFrame с историческими данными
        """
        url = f"{self.base_url}/history/engines/{engine}/markets/{market}/boards/{board}/securities/{ticker}.json"
        
        all_data = []
        start = 0
        
        async with aiohttp.ClientSession() as session:
            while True:
                params = {
                    "from": start_date,
                    "till": end_date,
                    "start": start,
                    "limit": 100
                }
                
                async with session.get(url, params=params) as response:
                    data = await response.json()
                    
                    # Получаем данные истории
                    history_data = data['history']
                    
                    if not history_data['data']:
                        break
                        
                    # Добавляем данные в общий список
                    all_data.extend(history_data['data'])
                    start += 100
                    
                    if len(history_data['data']) < 100:
                        break
        
        # Создаем DataFrame
        df = pd.DataFrame(all_data, columns=history_data['columns'])
        
        # Конвертируем даты и числовые значения
        df['TRADEDATE'] = pd.to_datetime(df['TRADEDATE'])
        numeric_columns = ['OPEN', 'HIGH', 'LOW', 'CLOSE', 'VALUE', 'VOLUME']
        df[numeric_columns] = df[numeric_columns].apply(pd.to_numeric)
        
        return df

    async def get_sector_history(
        self,
        sector_tickers: List[str],
        start_date: str,
        end_date: str,
        engine: str = "stock",
        market: str = "shares",
        board: str = "TQBR"
    ) -> Dict[str, pd.DataFrame]:
        """
        Получение исторических данных по всем тикерам сектора
        
        Args:
            sector_tickers: Список тикеров сектора
            start_date: Начальная дата в формате YYYY-MM-DD
            end_date: Конечная дата в формате YYYY-MM-DD
            engine: Торговый движок (по умолчанию stock)
            market: Рынок (по умолчанию shares)
            board: Режим торгов (по умолчанию TQBR)
            
        Returns:
            Словарь {тикер: DataFrame с историческими данными}
        """
        tasks = []
        for ticker in sector_tickers:
            task = self.get_security_history(
                ticker=ticker,
                start_date=start_date,
                end_date=end_date,
                engine=engine,
                market=market,
                board=board
            )
            tasks.append(task)
            
        results = await asyncio.gather(*tasks)
        return dict(zip(sector_tickers, results))

    def calculate_sector_index(
        self,
        sector_data: Dict[str, pd.DataFrame],
        weights: Optional[Dict[str, float]] = None
    ) -> pd.DataFrame:
        """
        Расчет индекса сектора на основе исторических данных входящих в него компаний
        
        Args:
            sector_data: Словарь с историческими данными по тикерам {тикер: DataFrame}
            weights: Словарь с весами компаний {тикер: вес}. Если None, веса будут равными
            
        Returns:
            DataFrame с рассчитанным индексом сектора
        """
        # Если веса не указаны, используем равные веса
        if weights is None:
            weights = {ticker: 1/len(sector_data) for ticker in sector_data.keys()}
            
        # Создаем DataFrame с датами и ценами закрытия для каждого тикера
        prices_df = pd.DataFrame()
        
        for ticker, df in sector_data.items():
            prices_df[ticker] = df.set_index('TRADEDATE')['CLOSE']
            
        # Рассчитываем относительное изменение цен
        returns_df = prices_df.pct_change()
        
        # Рассчитываем взвешенную доходность индекса
        weighted_returns = pd.DataFrame()
        for ticker in returns_df.columns:
            weighted_returns[ticker] = returns_df[ticker] * weights[ticker]
            
        index_returns = weighted_returns.sum(axis=1)
        
        # Рассчитываем значения индекса
        index_values = (1 + index_returns).cumprod() * 1000  # Начальное значение 1000
        
        # Создаем итоговый DataFrame
        result_df = pd.DataFrame({
            'INDEX_VALUE': index_values,
            'INDEX_RETURN': index_returns
        })
        
        return result_df

# Пример использования:
async def main():
    moex = MOEXHistoricalData()
    
    # Пример получения данных по одному тикеру
    sber_data = await moex.get_security_history(
        ticker="SBER",
        start_date="2023-01-01",
        end_date="2023-12-31"
    )
    print("Данные по SBER:")
    print(sber_data.head())
    
    # Пример получения данных по сектору
    finance_tickers = ['SBER', 'VTBR', 'MOEX']  # Укороченный список для примера
    sector_data = await moex.get_sector_history(
        sector_tickers=finance_tickers,
        start_date="2023-01-01",
        end_date="2023-12-31"
    )
    
    # Расчет индекса сектора
    sector_index = moex.calculate_sector_index(sector_data)
    print("\nИндекс финансового сектора:")
    print(sector_index.head())

if __name__ == "__main__":
    await main()

Данные по SBER:
  BOARDID  TRADEDATE SHORTNAME SECID  NUMTRADES         VALUE    OPEN     LOW  \
0    TQBR 2023-01-03  Сбербанк  SBER      55187  3.000248e+09  141.60  141.56   
1    TQBR 2023-01-04  Сбербанк  SBER      50172  2.419429e+09  141.85  140.75   
2    TQBR 2023-01-05  Сбербанк  SBER      45764  2.435171e+09  141.60  140.54   
3    TQBR 2023-01-06  Сбербанк  SBER      34184  1.504731e+09  141.39  140.90   
4    TQBR 2023-01-09  Сбербанк  SBER      75295  4.480148e+09  141.83  141.65   

     HIGH  LEGALCLOSEPRICE  ...  MARKETPRICE2  MARKETPRICE3  ADMITTEDQUOTE  \
0  143.25           141.65  ...        142.25        142.25         141.65   
1  142.28           141.30  ...        141.38        141.38         141.30   
2  141.84           141.31  ...        141.20        141.20         141.31   
3  141.62           141.14  ...        141.17        141.17         141.14   
4  142.99           142.43  ...        142.47        142.47         142.43   

      MP2VALTRD  MARKETPRICE

In [11]:
import pandas as pd
import requests
from datetime import datetime, timedelta
from typing import List, Dict, Optional
import asyncio
import aiohttp
import numpy as np

class MOEXHistoricalData:
    def __init__(self):
        self.base_url = "https://iss.moex.com/iss"
        
        # Словарь соответствия секторов и их индексов на MOEX
        self.sector_indices = {
            'metals_mining': 'MOEXMM',    # Индекс Металлов и добычи
            'oil_gas': 'MOEXOG',          # Индекс Нефти и газа
            'chemicals': 'MOEXCH',         # Индекс Химии и нефтехимии
            'electric_utilities': 'MOEXEU', # Индекс Электроэнергетики
            'telecom': 'MOEXTL',           # Индекс Телекоммуникаций
            'finance': 'MOEXFN',           # Индекс Финансов
            'consumer': 'MOEXCN',          # Индекс Потребительского сектора
            'transport': 'MOEXTN'          # Индекс Транспорта
        }
        
    async def get_security_history(
        self,
        ticker: str,
        start_date: str,
        end_date: str,
        engine: str = "stock",
        market: str = "shares",
        board: str = "TQBR"
    ) -> pd.DataFrame:
        """
        Получение исторических данных по отдельному тикеру
        
        Args:
            ticker: Тикер акции
            start_date: Начальная дата в формате YYYY-MM-DD
            end_date: Конечная дата в формате YYYY-MM-DD
            engine: Торговый движок (по умолчанию stock)
            market: Рынок (по умолчанию shares)
            board: Режим торгов (по умолчанию TQBR)
            
        Returns:
            DataFrame с историческими данными
        """
        url = f"{self.base_url}/history/engines/{engine}/markets/{market}/boards/{board}/securities/{ticker}.json"
        
        all_data = []
        start = 0
        
        async with aiohttp.ClientSession() as session:
            while True:
                params = {
                    "from": start_date,
                    "till": end_date,
                    "start": start,
                    "limit": 100
                }
                
                async with session.get(url, params=params) as response:
                    data = await response.json()
                    
                    # Получаем данные истории
                    history_data = data['history']
                    
                    if not history_data['data']:
                        break
                        
                    # Добавляем данные в общий список
                    all_data.extend(history_data['data'])
                    start += 100
                    
                    if len(history_data['data']) < 100:
                        break
        
        # Создаем DataFrame
        df = pd.DataFrame(all_data, columns=history_data['columns'])
        
        # Конвертируем даты и числовые значения
        df['TRADEDATE'] = pd.to_datetime(df['TRADEDATE'])
        numeric_columns = ['OPEN', 'HIGH', 'LOW', 'CLOSE', 'VALUE', 'VOLUME']
        df[numeric_columns] = df[numeric_columns].apply(pd.to_numeric)
        
        return df

    async def get_sector_history(
        self,
        sector_tickers: List[str],
        start_date: str,
        end_date: str,
        engine: str = "stock",
        market: str = "shares",
        board: str = "TQBR"
    ) -> Dict[str, pd.DataFrame]:
        """
        Получение исторических данных по всем тикерам сектора
        
        Args:
            sector_tickers: Список тикеров сектора
            start_date: Начальная дата в формате YYYY-MM-DD
            end_date: Конечная дата в формате YYYY-MM-DD
            engine: Торговый движок (по умолчанию stock)
            market: Рынок (по умолчанию shares)
            board: Режим торгов (по умолчанию TQBR)
            
        Returns:
            Словарь {тикер: DataFrame с историческими данными}
        """
        tasks = []
        for ticker in sector_tickers:
            task = self.get_security_history(
                ticker=ticker,
                start_date=start_date,
                end_date=end_date,
                engine=engine,
                market=market,
                board=board
            )
            tasks.append(task)
            
        results = await asyncio.gather(*tasks)
        return dict(zip(sector_tickers, results))

    async def get_official_sector_index(
        self,
        sector: str,
        start_date: str,
        end_date: str
    ) -> pd.DataFrame:
        """
        Получение официального отраслевого индекса с MOEX
        
        Args:
            sector: Название сектора (ключ из словаря sector_indices)
            start_date: Начальная дата в формате YYYY-MM-DD
            end_date: Конечная дата в формате YYYY-MM-DD
            
        Returns:
            DataFrame с данными индекса
        """
        if sector not in self.sector_indices:
            raise ValueError(f"Неизвестный сектор: {sector}. Доступные секторы: {list(self.sector_indices.keys())}")
            
        index_ticker = self.sector_indices[sector]
        url = f"{self.base_url}/history/engines/stock/markets/index/securities/{index_ticker}.json"
        
        all_data = []
        start = 0
        
        async with aiohttp.ClientSession() as session:
            while True:
                params = {
                    "from": start_date,
                    "till": end_date,
                    "start": start,
                    "limit": 100
                }
                
                async with session.get(url, params=params) as response:
                    data = await response.json()
                    
                    history_data = data['history']
                    
                    if not history_data['data']:
                        break
                        
                    all_data.extend(history_data['data'])
                    start += 100
                    
                    if len(history_data['data']) < 100:
                        break
        
        df = pd.DataFrame(all_data, columns=history_data['columns'])
        
        # Конвертируем даты и числовые значения
        df['TRADEDATE'] = pd.to_datetime(df['TRADEDATE'])
        numeric_columns = ['OPEN', 'HIGH', 'LOW', 'CLOSE', 'VALUE', 'VOLUME']
        df[numeric_columns] = df[numeric_columns].apply(pd.to_numeric)
        
        return df

    def calculate_sector_index(
        self,
        sector_data: Dict[str, pd.DataFrame],
        weights: Optional[Dict[str, float]] = None
    ) -> pd.DataFrame:
        """
        Расчет индекса сектора на основе исторических данных входящих в него компаний
        
        Args:
            sector_data: Словарь с историческими данными по тикерам {тикер: DataFrame}
            weights: Словарь с весами компаний {тикер: вес}. Если None, веса будут равными
            
        Returns:
            DataFrame с рассчитанным индексом сектора
        """
        # Если веса не указаны, используем равные веса
        if weights is None:
            weights = {ticker: 1/len(sector_data) for ticker in sector_data.keys()}
            
        # Создаем DataFrame с датами и ценами закрытия для каждого тикера
        prices_df = pd.DataFrame()
        
        for ticker, df in sector_data.items():
            prices_df[ticker] = df.set_index('TRADEDATE')['CLOSE']
            
        # Рассчитываем относительное изменение цен
        returns_df = prices_df.pct_change()
        
        # Рассчитываем взвешенную доходность индекса
        weighted_returns = pd.DataFrame()
        for ticker in returns_df.columns:
            weighted_returns[ticker] = returns_df[ticker] * weights[ticker]
            
        index_returns = weighted_returns.sum(axis=1)
        
        # Рассчитываем значения индекса
        index_values = (1 + index_returns).cumprod() * 1000  # Начальное значение 1000
        
        # Создаем итоговый DataFrame
        result_df = pd.DataFrame({
            'INDEX_VALUE': index_values,
            'INDEX_RETURN': index_returns
        })
        
        return result_df

# Пример использования:
async def main():
    moex = MOEXHistoricalData()
    
    # Пример получения данных по одному тикеру
    sber_data = await moex.get_security_history(
        ticker="SBER",
        start_date="2023-01-01",
        end_date="2023-12-31"
    )
    print("Данные по SBER:")
    print(sber_data.head())
    
    # Пример получения данных по сектору
    finance_tickers = ['SBER', 'VTBR', 'MOEX']  # Укороченный список для примера
    sector_data = await moex.get_sector_history(
        sector_tickers=finance_tickers,
        start_date="2023-01-01",
        end_date="2023-12-31"
    )
    
    # Расчет индекса сектора
    sector_index = moex.calculate_sector_index(sector_data)
    print("\nИндекс финансового сектора:")
    print(sector_index.head())

if __name__ == "__main__":
    await main()

Данные по SBER:
  BOARDID  TRADEDATE SHORTNAME SECID  NUMTRADES         VALUE    OPEN     LOW  \
0    TQBR 2023-01-03  Сбербанк  SBER      55187  3.000248e+09  141.60  141.56   
1    TQBR 2023-01-04  Сбербанк  SBER      50172  2.419429e+09  141.85  140.75   
2    TQBR 2023-01-05  Сбербанк  SBER      45764  2.435171e+09  141.60  140.54   
3    TQBR 2023-01-06  Сбербанк  SBER      34184  1.504731e+09  141.39  140.90   
4    TQBR 2023-01-09  Сбербанк  SBER      75295  4.480148e+09  141.83  141.65   

     HIGH  LEGALCLOSEPRICE  ...  MARKETPRICE2  MARKETPRICE3  ADMITTEDQUOTE  \
0  143.25           141.65  ...        142.25        142.25         141.65   
1  142.28           141.30  ...        141.38        141.38         141.30   
2  141.84           141.31  ...        141.20        141.20         141.31   
3  141.62           141.14  ...        141.17        141.17         141.14   
4  142.99           142.43  ...        142.47        142.47         142.43   

      MP2VALTRD  MARKETPRICE

In [17]:
moex = MOEXHistoricalData()

# Получение официального индекса металлургического сектора
metals_index = await moex.get_official_sector_index(
    sector='metals_mining',
    start_date="2018-01-01",
    end_date="2024-12-01"
)

metals_index

BOARDID   SECID  TRADEDATE                 SHORTNAME  \
0       SNDX  MOEXMM 2018-01-03  Индекс металлов и добычи   
1       SNDX  MOEXMM 2018-01-04  Индекс металлов и добычи   
2       SNDX  MOEXMM 2018-01-05  Индекс металлов и добычи   
3       SNDX  MOEXMM 2018-01-09  Индекс металлов и добычи   
4       SNDX  MOEXMM 2018-01-10  Индекс металлов и добычи   
...      ...     ...        ...                       ...   
1726    SNDX  MOEXMM 2024-11-25  Индекс металлов и добычи   
1727    SNDX  MOEXMM 2024-11-26  Индекс металлов и добычи   
1728    SNDX  MOEXMM 2024-11-27  Индекс металлов и добычи   
1729    SNDX  MOEXMM 2024-11-28  Индекс металлов и добычи   
1730    SNDX  MOEXMM 2024-11-29  Индекс металлов и добычи   

                                   NAME    CLOSE     OPEN     HIGH      LOW  \
0     Индекс МосБиржи металлов и добычи  5936.24  5856.03  5936.24  5854.65   
1     Индекс МосБиржи металлов и добычи  6009.94  5940.37  6009.94  5935.96   
2     Индекс МосБиржи металлов и добычи  5990.95  5988.89  5999.54  5956.60   
3     Индекс МосБиржи металлов и добычи  6022.02  5987.07  6038.40  5972.35   
4     Индекс МосБиржи металлов и добычи  6026.48  6010.55  6030.44  5971.82   
...                                 ...      ...      ...      ...      ...   
1726  Индекс МосБиржи металлов и добычи  5870.08  6064.07  6079.37  5853.41   
1727  Индекс МосБиржи металлов и добычи  5704.27  5848.86  5905.42  5688.20   
1728  Индекс МосБиржи металлов и добычи  5802.04  5744.94  5881.01  5625.11   
1729  Индекс МосБиржи металлов и добычи  5942.27  5945.16  6004.23  5850.80   
1730  Индекс МосБиржи металлов и добычи  5993.04  5952.51  6046.36  5936.67   

             VALUE  DURATION  YIELD  DECIMALS  CAPITALIZATION CURRENCYID  \
0     3.564566e+09       0.0    0.0         2    1.066002e+12        RUB   
1     5.683395e+09       0.0    0.0         2    1.079237e+12        RUB   
2     5.170026e+09       0.0    0.0         2    1.075825e+12        RUB   
3     7.377819e+09       0.0    0.0         2    1.081405e+12        RUB   
4     5.791063e+09       0.0    0.0         2    1.082207e+12        RUB   
...            ...       ...    ...       ...             ...        ...   
1726  1.376984e+10       0.0    0.0         2    5.920869e+11        RUB   
1727  1.967379e+10       0.0    0.0         2    5.753617e+11        RUB   
1728  2.587743e+10       0.0    0.0         2    5.852239e+11        RUB   
1729  1.858550e+10       0.0    0.0         2    5.993674e+11        RUB   
1730  1.329048e+10       0.0    0.0         2    6.044888e+11        RUB   

           DIVISOR TRADINGSESSION  VOLUME  
0     1.795751e+08              3     NaN  
1     1.795751e+08              3     NaN  
2     1.795751e+08              3     NaN  
3     1.795751e+08              3     NaN  
4     1.795751e+08              3     NaN  
...            ...            ...     ...  
1726  1.008651e+08              3     NaN  
1727  1.008651e+08              3     NaN  
1728  1.008651e+08              3     NaN  
1729  1.008651e+08              3     NaN  
1730  1.008651e+08              3     NaN  

[1731 rows x 18 columns]

In [32]:
from config import sector_tickers
hi = [ticker for tickers in sector_tickers.values() for ticker in tickers]
print(hi)

['ALRS', 'AMEZ', 'BELO', 'BLNG', 'CHEP', 'CHMF', 'CHMK', 'CHZN', 'ENPG', 'GMKN', 'KBTK', 'KOGK', 'LNZL', 'LNZLP', 'MAGN', 'MGOK', 'MTLR', 'MTLRP', 'NLMK', 'PGIL', 'PLZL', 'PMTL', 'POGR', 'POLY', 'RASP', 'RUAL', 'RUALR', 'SELG', 'SELGP', 'TRMK', 'UGLD', 'UNKL', 'VSMO', 'VSMZ', 'BANE', 'BANEP', 'GAZP', 'JNOSP', 'KRKNP', 'LKOH', 'MFGS', 'MFGSP', 'NOTK', 'NVTK', 'RITK', 'RNFT', 'RNHSP', 'ROSN', 'SIBN', 'SNGS', 'SNGSP', 'TATN', 'TATNP', 'TNBP', 'TNBPP', 'TRMK', 'TRNFP', 'AKRN', 'AZKM', 'DGBZ', 'DGBZP', 'KAZT', 'KZOS', 'KZOSP', 'MGNZ', 'NKNC', 'NKNCP', 'OMSH', 'PHOR', 'SILV', 'URKA', 'YASH', 'ARSB', 'BEGY', 'DVEC', 'EESR', 'EESRP', 'ELFV', 'ENRU', 'EONR', 'FEES', 'HYDR', 'IRAO', 'IRGZ', 'KISB', 'KRNG', 'KRSG', 'LSNG', 'LSNGP', 'MGSV', 'MRKC', 'MRKH', 'MRKK', 'MRKP', 'MRKS', 'MRKU', 'MRKV', 'MRKY', 'MRKZ', 'MSNG', 'MSRS', 'MSSB', 'MSSV', 'OGK1', 'OGK2', 'OGK4', 'OGK6', 'OGKA', 'OGKB', 'OGKC', 'OGKD', 'OGKE', 'OGKF', 'RSTI', 'RSTIP', 'SAGO', 'SARE', 'SVER', 'TGKA', 'TGKB', 'TGKD', 'TGKE', 'TGK